# EMET2007 Week 12

Use the file gdp_us_2024.csv, a time series of US real GDP, provided by FRED (Federal Reserve Economic Data) to produce a forecast for 2024:Q2.

## Imports and loading data

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import statsmodels.formula.api as smf
from statsmodels.graphics.tsaplots import plot_acf
from statsmodels.tsa.ar_model import AutoReg
from statsmodels.tsa.stattools import adfuller
import numpy as np

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')
# df = pd.read_csv('drive/MyDrive/EMET2007/datasets/gdp_us_2024.csv')

In [ ]:
df = pd.read_csv('../datasets/gdp_us_2024.csv')

Run this cell once you've loaded the data:

In [ ]:
df['date'] = pd.to_datetime(df['DATE'], format='%Y-%m-%d')
df.index = pd.DatetimeIndex(df.date, name='quarter').to_period('Q')

We'll use the function `ar1_pseudo` from the end of last week:

In [ ]:
def ar1_pseudo(input_df, y, startdate):
    """
    Pseudo out-of-sample forecasts and errors based on AR(1) model

    Returns: 
    forecasts: time series of pseudo out-of-sample forecasts
    forecast_errors: time series of pseudo out-of-sample forecast errors

    Arguments:
    df: a pandas DataFrame containing:
            the variable of interest, y
            an index with frequency 'Q' like we created at the start
    y: a string of the name of the variable of interest
    startdate: a string of the first quarter we want to
                produce a forecast for (e.g. '2005Q1')
    """
    
    # Create the variables we need
    df = pd.DataFrame()  # empty pandas df
    df['y'] = input_df[y]  # get dependent variable
    df['lag_y'] = df.y.shift(1)  # create its first lag
    df['trend'] = range(len(input_df[y]))  # create trend variable
    # create empty column for each (s + 1) forecast to go in
    df['next_forecast'] = pd.Series(dtype='float64')
    
    # Get starting quarter
    start_period = pd.Period(startdate, freq='Q')
    
    # Iterate over df rows
    for i, row in df.iterrows():
        # Ignore all rows that are before period s
        if row.name < start_period - 1:
                continue

        # Otherwise:
        # create subsample containing all rows in periods
        # up to and including s
        df_sub = df[df.index <= row.name]  
        
        # fit AR1 model using that subsample
        ar_tmp = smf.ols(f'y ~ lag_y + trend', 
                            data = df_sub,
                            missing='drop').fit()
        
        # specify the values we need to feed to the model for our
        # forecast
        df_aux = {'lag_y' : row.y,
                  'trend' : row.trend,
                 }
        prediction = ar_tmp.predict(df_aux)  # create the forecast
        df.at[i, 'next_forecast'] = prediction[0]  # modify the df

    # Add another row to the df to accommodate the final forecast
    df.loc[df.iloc[-1].name + 1,:] = np.nan
    # Shift the 'next_forecast' variable so we get a value for
    # 'forecast' in the appropriate period
    df['forecast'] = df.next_forecast.shift(1)
    # Calculate each forecast error
    df['forecast_error'] = df.y - df.forecast
    
    # Only keep the relevant columns and return the df
    results_df = df[['forecast', 'forecast_error']].copy()
    results_df['date'] = results_df.index.to_timestamp()  
    # for less typing when plotting
    return results_df

In [ ]:
df = df.rename({'GDPC1' : 'gdp'}, axis=1)

## Initial plotting

Let's first plot the GDP series. What do you learn about the time series?

In [ ]:
fig, ax = plt.subplots(figsize=(10,5))

ax.plot(df.date, df.gdp)
ax.set_xlabel('Time')
ax.set_ylabel('GDP ($bn, chained 2012 dollars)')
ax.set_title('Time series: US real GDP')
plt.show()

What if we want to focus on the GDP time series beginning in 2000Q1?

In [ ]:
df_2000 = df[df.index >= '2000Q1']
fig, ax = plt.subplots(figsize=(10,5))
ax.plot(df_2000.date, df_2000.gdp)
ax.set_xlabel('Time')
ax.set_ylabel('GDP ($bn, chained 2012 dollars)')
ax.set_title('Time series: US real GDP')
plt.show()

This shows us more clearly the recessions during the 2007-2008 GFC and the 2020-2023 Covid pandemic.

## Forecasting GDP for current period (naïve approach)

In [ ]:
df['l1_gdp'] =  df.gdp.shift(1)
forecast_ar1 = smf.ols('gdp ~ l1_gdp', data=df, missing='drop').fit(use_t=False)
forecast_ar1.summary()

With this regression, we can make a prediction based on the last term of GDP.  

But before that, let's notice that the autoregressive coefficient is very close to 1.  This could indicate that there is a unit root in the time series.

If we use a model with a unit root, our predictions will be biased.  At this stage we do not know if it is a deterministic or stochastic trend, so we test for the unit root.

In [ ]:
adfuller(df.gdp, maxlag = 0, regression='ct')

Comparing the -1.5756 with the -3.41 DF critical value, we cannot reject the null (can also come to this conclusion by looking at the p-value in the above output).  Therefore we cannot use the GDP time series to make our forecasts.

### Create first differences of GDP, i.e. derive the GDP growth rate

In [ ]:
df['log_gdp'] = np.log(df.gdp)
df['gdp_growth'] = 400 * (df.log_gdp - df.log_gdp.shift(1))

### Repeat initial plotting

In [ ]:
fig, ax = plt.subplots(figsize=(10,5))

ax.plot(df.date, df.gdp_growth)
ax.set_xlabel('Time')
ax.set_ylabel('GDP growth rate (annualised, %)')
ax.set_title('Time series: US real GDP growth rate')
plt.show()

In [ ]:
df_2000 = df[df.index >= '2000Q1']
fig, ax = plt.subplots(figsize=(10,5))

ax.plot(df_2000.date, df_2000.gdp_growth)
ax.set_xlabel('Time')
ax.set_ylabel('GDP growth rate (annualised, %)')
ax.set_title('Time series: US real GDP growth rate')
plt.show()

We can see the extraordinary growth rate in GDP around the pandemic.  Recall that these are **annualised** quarterly values; there were not actually ~40% decreases in GDP during any year.

Because that period changed our trend significantly, may want to restrict our plot to view the period before 2020:

In [ ]:
df_2019 = df[df.index <= '2019Q4']
fig, ax = plt.subplots(figsize=(10,5))

ax.plot(df_2019.date, df_2019.gdp_growth)
ax.set_xlabel('Time')
ax.set_ylabel('GDP growth rate (annualised, %)')
ax.set_title('Time series: US real GDP growth rate')
ax.grid()
plt.show()

Here we can see various recessions - and we can directly compare them to e.g. https://wikiless.org/wiki/List_of_recessions_in_the_United_States?lang=en#Great_Depression_onward_(1929%E2%80%93present)

Some notable ones are: 
- 1973-75, oil crisis
- 1980/1981-82, another energy crisis + Volcker
- 2001, low magnitude recession following dotcom bust
- 2007-09, GFC

Back to our main focus for this workshop, we can test this series for a unit root:

In [ ]:
adfuller(df.gdp_growth.dropna(), maxlag = 0, regression='ct')

- ADF test stat = -15.8 < -3.41
- p-value close to zero
- => reject null hypothesis of a unit root for GDP growth

We can therefore use this time series and our pseudo out-of-sample forecast function to create our forecast.

In [ ]:
results_df = ar1_pseudo(df, 'gdp_growth', '2005Q1')
results_df

- The values returned up to 2024:Q1 are all predictions
- But the one returned for 2024:Q2 is a forecast

In [ ]:
fig, ax = plt.subplots(figsize=(10, 6))

ax.plot(results_df.date, results_df.forecast, color='darkblue')
df_2000 = df[df.index >= '2000Q1']
ax.plot(df_2000.date, df_2000.gdp_growth, color='green')
ax.set_xlabel('Date')
ax.set_ylabel('GDP growth (annualised, %)')
ax.set_title('Realisations and pseudo out-of-sample forecasts for GDP growth (2005:Q1 to 2024:Q2)')
plt.show()

This forecast looks fairly flat.  We may want to restrict our plot to the pre-pandemic period so we can see any trends more clearly:

In [ ]:
fig, ax = plt.subplots(figsize=(10, 6))

results_df_19 = results_df[(results_df.index >= '2000Q1') & (results_df.index <= '2019Q4')]
ax.plot(results_df_19.date, results_df_19.forecast, color='darkblue')
df_19 = df[(df.index >= '2000Q1') & (df.index <= '2019Q4')]
ax.plot(df_19.date, df_19.gdp_growth, color='green')
ax.set_xlabel('Date')
ax.set_ylabel('GDP growth (annualised, %)')
ax.set_title('Realisations and pseudo out-of-sample forecasts for inflation (2005:Q1 to 2020:Q1)')
plt.show()

#### Example: AR(4) pseudo function

In [ ]:
def ar_k_pseudo(input_df, y, startdate, lags=1):
    """
    Pseudo out-of-sample forecasts and errors based on AR(k) model

    Returns: 
    forecasts: time series of pseudo out-of-sample forecasts
    forecast_errors: time series of pseudo out-of-sample forecast errors

    Arguments:
    df: a pandas DataFrame containing:
            the variable of interest, y
            an index with frequency 'Q' like we created above
    y: a string of the name of the variable of interest
    startdate: a string of the first quarter we want to
                produce a forecast for (e.g. '2005Q1')
    lags: number of lags (k)
    """
    
    # Create the variables we need
    df = pd.DataFrame()  # empty pandas df
    df['y'] = input_df[y]  # get dependent variable
    for k in range(1, lags + 1):
        df[f'lag{k}_y'] = df.y.shift(k)  # create the kth lag
    df['trend'] = range(len(input_df[y]))  # create trend variable
    # create empty column for each (s + 1) forecast to go in
    df['next_forecast'] = pd.Series(dtype='float64')
    
    # Get starting quarter
    start_period = pd.Period(startdate, freq='Q')
    
    # Iterate over df rows
    for i, row in df.iterrows():
        # Ignore all rows that are before period s
        if row.name < start_period - 1:
                continue

        # Otherwise:
        # create subsample containing all rows in periods
        # up to and including s
        df_sub = df[df.index <= row.name]  
        
        formula = 'y ~ '
        for k in range(1, lags + 1):
            formula += f'lag{k}_y + '
        formula += 'trend'
        
        # fit AR(k) model using that subsample
        ar_tmp = smf.ols(formula, 
                            data = df_sub,
                            missing='drop').fit()
        
        # specify the values we need to feed to the model for our
        # forecast
        df_aux = {
                    'lag1_y' : row.y,
                    'trend' : row.trend
                }
        for k in range(2, lags + 1):
            df_aux[f'lag{k}_y'] = row[f'lag{k - 1}_y']
        prediction = ar_tmp.predict(df_aux)  # create the forecast
        df.at[i, 'next_forecast'] = prediction[0]  # modify the df
      
    # Add another row to the df to accommodate the final forecast
    df.loc[df.iloc[-1].name + 1,:] = np.nan
    # Shift the 'next_forecast' variable so we get a value for
    # 'forecast' in the appropriate period
    df['forecast'] = df.next_forecast.shift(1)
    # Calculate each forecast error
    df['forecast_error'] = df.y - df.forecast
    
    # Only keep the relevant columns and return the results df
    results_df = df[['forecast', 'forecast_error']].copy()
    results_df['date'] = results_df.index.to_timestamp()  
    # for less typing when plotting
    return results_df

In [ ]:
results2_df = ar_k_pseudo(df, 'gdp_growth', '2005Q1', lags=4)
results2_df.tail(72)

In [ ]:
fig, ax = plt.subplots(figsize=(10, 6))

ax.plot(results2_df.date, results2_df.forecast, 
        color='darkblue', label='AR(4) pseudo forecast')
df_2000 = df[df.index >= '2000Q1']
ax.plot(df_2000.date, df_2000.gdp_growth, 
        color='green', label='Realised GDP growth')
ax.set_xlabel('Date')
ax.set_ylabel('GDP growth (annualised, %)')
ax.set_title('Realisations and pseudo out-of-sample forecasts for GDP growth (2005:Q1 to 2024:Q2)')
plt.show()

#### Comparison of performance to AR(1) model
- AR(1) model forecasts 1.51% for this quarter
- AR(4) model forecasts 1.6% for this quarter

Which is better (or is another lag better)?
- Not covered in this course
- Depends on the trend of the data itself

Note: AR(4) prediction is usually going to be smoother than AR(1) prediction

## Convert forecast back to GDP value

In [ ]:
ar1_forecast_gr = results_df.forecast[-1]
ar4_forecast_gr = results2_df.forecast[-1]
ar1_forecast_gr, ar4_forecast_gr

In [ ]:
ar1_forecast = np.exp(np.log(df.gdp[-1]) + (ar1_forecast_gr / 400))
ar4_forecast = np.exp(np.log(df.gdp[-1]) + (ar4_forecast_gr / 400))
ar1_forecast, ar4_forecast

Remember, the units here are 'Billions of Chained 2012 Dollars'.  